In [1]:
import os
from dotenv import load_dotenv
from langchain_groq import ChatGroq
from langchain.prompts import PromptTemplate

/Users/harshitsundriyal/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(


In [2]:
from langgraph.graph import START, StateGraph, MessagesState
from langgraph.prebuilt import (tools_condition,
                                ToolNode)
from langchain_groq import ChatGroq
from langchain_huggingface import HuggingFaceEmbeddings, ChatHuggingFace, HuggingFaceEndpoint
from langchain_community.tools.tavily_search import TavilySearchResults
from langchain_core.messages import SystemMessage, HumanMessage
from langchain.tools import tool
from langchain_community.document_loaders import (
    WikipediaLoader,
    GoogleDriveLoader,
    ArxivLoader)


load_dotenv()

True

In [3]:
llm = ChatGroq(
    temperature=0,
    model_name="qwen-qwq-32b",  # Updated to working model
    groq_api_key=os.getenv("GROQ_API_KEY")
)

In [4]:
# Initialize Tavily tool
search_tool = TavilySearchResults()

In [5]:
# Run a test query
query = "What is the capital of India?"
results = search_tool.run(query)

# Print results
print("Tavily Search Results:")
print(results)

Tavily Search Results:
[{'title': 'What is the capital of India? States and union territories explained.', 'url': 'https://www.usatoday.com/story/news/world/2023/05/24/what-is-the-capital-of-india/70195720007/', 'content': 'Want to learn more about the soon-to-be most populous country? Here’s some interesting information about how India is organized.\n\nWhat is the capital of India?\n\nThe capital of India is New Delhi, located in the north-central part of the country to the west of the Yamuna River.\n\nCalcutta (now Kolkata, the capital of West Bengal) was the country’s capital until 1911 when King George V declared Delhi the new capital and construction of New Delhi began. [...] When the national government achieved independence in 1947, New Delhi became the capital.\n\nMumbai, the state capital of Maharashtra, is often considered the financial capital of India because of its role in the national and international economy.\n\nHow many states are in India?\n\nIndia is home to 28 state

In [6]:
@tool
def get_weather(location: str) -> str:
    """Fetch the current weather information for a given location using Tavily search."""
    query = f"current weather in {location}"
    results = search_tool.run(query)
    return results

In [7]:
get_weather.invoke("Delhi")

[{'title': 'Weather in Delhi',
  'url': 'https://www.weatherapi.com/',
  'content': "{'location': {'name': 'Delhi', 'region': 'Ontario', 'country': 'Canada', 'lat': 42.85, 'lon': -80.5, 'tz_id': 'America/Toronto', 'localtime_epoch': 1746246286, 'localtime': '2025-05-03 00:24'}, 'current': {'last_updated_epoch': 1746245700, 'last_updated': '2025-05-03 00:15', 'temp_c': 10.4, 'temp_f': 50.7, 'is_day': 0, 'condition': {'text': 'Overcast', 'icon': '//cdn.weatherapi.com/weather/64x64/night/122.png', 'code': 1009}, 'wind_mph': 6.7, 'wind_kph': 10.8, 'wind_degree': 39, 'wind_dir': 'NE', 'pressure_mb': 1013.0, 'pressure_in': 29.91, 'precip_mm': 0.0, 'precip_in': 0.0, 'humidity': 74, 'cloud': 0, 'feelslike_c': 9.0, 'feelslike_f': 48.2, 'windchill_c': 5.9, 'windchill_f': 42.7, 'heatindex_c': 8.2, 'heatindex_f': 46.7, 'dewpoint_c': 4.4, 'dewpoint_f': 40.0, 'vis_km': 10.0, 'vis_miles': 6.0, 'uv': 0.0, 'gust_mph': 10.5, 'gust_kph': 16.9}}",
  'score': 0.9573658},
 {'title': 'New Delhi 14 Day Extend

In [8]:
from langchain_core.prompts import ChatPromptTemplate
from langchain_core.runnables import Runnable


# Define a prompt template
recommendation_prompt = ChatPromptTemplate.from_template("""
You are a helpful assistant that gives weather-based advice.

Given the current weather condition: "{weather_condition}", provide:
1. Clothing or activity recommendations suited for this weather.
2. At least one health tip to stay safe or comfortable in this condition.

Be concise and clear.
""")

# Combine prompt and LLM into a runnable
recommendation_chain: Runnable = recommendation_prompt | llm

# Wrap it as a LangChain tool
@tool
def get_recommendation(weather_condition: str) -> str:
    """Give activity/clothing recommendations and health tips based on the weather condition using an LLM."""
    return recommendation_chain.invoke({"weather_condition": weather_condition})

In [9]:
get_recommendation.invoke("sunny and 30 degrees Celsius")

AIMessage(content="\n<think>\nOkay, the user wants advice for sunny 30°C weather. Let me start by thinking about clothing. It's warm but not super hot yet. Light fabrics like cotton or linen would be good because they're breathable. Shorts and a t-shirt are obvious, but maybe mention specific types like loose-fitting to allow airflow. A hat would provide shade, maybe a wide-brimmed one to protect the face and neck. Sunglasses are a must to shield the eyes from UV rays.\n\nActivities? Outdoor stuff obviously. Maybe suggest water activities like swimming since it's hot. Barbecues or picnics in the park could be nice. But also think about timing—like suggesting to do outdoor exercises in the morning or evening to avoid the midday sun. Maybe mention things like hiking or cycling but again with the time consideration.\n\nHealth tips. Hydration is key. Need to remind to drink water even if not thirsty. Sunscreen with high SPF, reapplying every few hours. Maybe mention avoiding the sun during

In [10]:
from langchain_community.document_loaders import WikipediaLoader
@tool
def wiki_search(query : str) -> str:
    """Search Wikipedia for a given query and return the summary.
    Args:
        query (str): The search query.
    """
    
    search_docs = WikipediaLoader(query=query, load_max_docs=1).load()
    formatted_search_docs = "\n\n----\n\n".join(
        [
            f'<Document Source="{doc.metadata["source"]}" page="{doc.metadata.get("page", "")}">\n{doc.page_content}\n</Document>'
            for doc in search_docs
        ])
    return formatted_search_docs

In [11]:
# ! pip install wikipedia

In [12]:
import wikipedia
wiki_search.invoke("AI Agents")

'<Document Source="https://en.wikipedia.org/wiki/Agentic_AI" page="">\nAgentic AI is a class of artificial intelligence that focuses on autonomous systems that can make decisions and perform tasks without human intervention. The independent systems automatically respond to conditions, to produce process results. The field is closely linked to agentic automation, also known as agent-based process management systems, when applied to process automation. Applications include software development, customer support, cybersecurity and business intelligence. \n\n\n== Overview ==\nThe core concept of agentic AI is the use of AI agents to perform automated tasks but without human intervention. While robotic process automation (RPA) and AI agents can be programmed to automate specific tasks or support rule-based decisions, the rules are usually fixed. Agentic AI operates independently, making decisions through continuous learning and analysis of external data and complex data sets. Functioning ag

In [13]:
@tool
def web_search(query: str) -> str:
    """Search the web for a given query and return the summary.
    Args:
        query (str): The search query.
    """
    
    search_tool = TavilySearchResults()
    result = search_tool.run(query)
    return result[0]['content']

In [14]:
output = web_search.invoke("AI Agents")
print(output)

AI agents are a type of artificial intelligence (AI) system that can understand and respond to customer inquiries without human intervention. They are created using an agent builder, like Agentforce, and rely on machine learning and natural language processing (NLP) to handle a wide range of tasks. These intelligent agents can include anything from answering simple questions to resolving complex issues — even multi-tasking. Most importantly, AI agents can continuously improve their own [...] Want better, fully-optimized marketing campaigns? AI agents can help your marketing team build better campaigns — faster. With Agentforce Campaigns, AI agents generate a campaign brief and target audience segment, then create relevant content speaking to those audiences. AI can even build a customer journey in Flow. AI agents also continually analyze campaign performance against your key performance indicators and proactively recommend improvements.


In [18]:
@tool
def add(x: int, y: int) -> int:
    """Add two numbers.
    Args:
        x (int): First number.
        y (int): Second number.
        """

    return x + y

@tool
def subtract(x: int, y: int) -> int:
    """Subtract two numbers.
    Args:
        x (int): First number.
        y (int): Second number.
        """

    return x - y

@tool
def multiply(x: int, y: int) -> int:
    """Multiply two numbers.
    Args:
        x (int): First number.
        y (int): Second number.
        """

    return x * y

@tool
def divide(x: int, y: int) -> float:
    """Divide two numbers.
    Args:
        x (int): First number.
        y (int): Second number.
        """

    if y == 0:
        raise ValueError("Cannot divide by zero.")
    return x / y

@tool
def square(x: int) -> int:
    """Square a number.
    Args:
        x (int): The number to be squared.
        """

    return x * x

@tool
def cube(x: int) -> int:
    """Cube a number.
    Args:
        x (int): The number to be cubed.
        """

    return x * x * x

@tool
def power(x: int, y: int) -> int:
    """Raise a number to the power of another number.
    Args:
        x (int): The base number.
        y (int): The exponent.
        """

    return x ** y

@tool
def factorial(n: int) -> int:
    """Calculate the factorial of a number.
    Args:
        n (int): The number to calculate the factorial for.
        """

    if n < 0:
        raise ValueError("Factorial is not defined for negative numbers.")
    if n == 0 or n == 1:
        return 1
    result = 1
    for i in range(2, n + 1):
        result *= i
    return result

@tool
def mean(numbers: list) -> float:
    """Calculate the mean of a list of numbers.
    Args:
        numbers (list): A list of numbers.
        """

    if not numbers:
        raise ValueError("The list is empty.")
    return sum(numbers) / len(numbers)

@tool
def standard_deviation(numbers: list) -> float:
    """Calculate the standard deviation of a list of numbers.
    Args:
        numbers (list): A list of numbers.
        """

    if not numbers:
        raise ValueError("The list is empty.")
    mean_value = mean(numbers)
    variance = sum((x - mean_value) ** 2 for x in numbers) / len(numbers)
    return variance ** 0.5

In [29]:
# !pip install chromadb

In [25]:
from langchain_community.vectorstores import Chroma
from langchain.embeddings import HuggingFaceEmbeddings
from langchain.tools.retriever import create_retriever_tool
from langchain_core.documents import Document
import os

# Create embeddings
embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-mpnet-base-v2")

# Example documents to index
documents = [
    Document(page_content="What is artificial intelligence?"),
    Document(page_content="Explain how AI agents operate."),
]

# Create a Chroma vector store (in memory or persistent)
vector_store = Chroma.from_documents(documents, embeddings, persist_directory="./chroma_db")

# (Optional) Persist the DB to disk
vector_store.persist()

# Create the retriever tool
create_retriever_tool = create_retriever_tool(
    retriever=vector_store.as_retriever(),
    name="Question_Search",
    description="A tool to retrieve similar questions using ChromaDB vector store.",
)

/var/folders/r6/l4km4ywx28zb1dkl0yp8fyn80000gn/T/ipykernel_1001/4015992125.py:20: LangChainDeprecationWarning: Since Chroma 0.4.x the manual persistence method is no longer supported as docs are automatically persisted.
  vector_store.persist()


In [26]:
vector_store = Chroma(persist_directory="./chroma_db", embedding_function=embeddings)

/var/folders/r6/l4km4ywx28zb1dkl0yp8fyn80000gn/T/ipykernel_1001/1571824264.py:1: LangChainDeprecationWarning: The class `Chroma` was deprecated in LangChain 0.2.9 and will be removed in 1.0. An updated version of the class exists in the :class:`~langchain-chroma package and should be used instead. To use it run `pip install -U :class:`~langchain-chroma` and import as `from :class:`~langchain_chroma import Chroma``.
  vector_store = Chroma(persist_directory="./chroma_db", embedding_function=embeddings)


In [27]:
tools = [
    multiply,
    add,
    subtract,
    divide,
    square,
    cube,
    power,
    factorial,
    mean,
    standard_deviation,
    get_weather,
    get_recommendation,
    wiki_search,
    web_search
]

In [31]:
from langgraph.graph import StateGraph, START
from langgraph.prebuilt import ToolNode
from langchain_groq import ChatGroq
from langchain_core.messages import HumanMessage
from configs.prompt import Agent_prompt_template

def build_graph():
    """Build the graph using Groq and custom prompt/tools setup"""

    # Initialize the LLM
    llm = ChatGroq(
        model="qwen-qwq-32b",
        temperature=0
    )

    # Bind tools to LLM
    llm_with_tools = llm.bind_tools(tools)

    # Define assistant node
    def assistant(state: MessagesState):
        """Assistant node"""
        return {"messages": [llm_with_tools.invoke(state["messages"])]}

    # Define retriever node
    def retriever(state: MessagesState):
        """Retriever node"""
        similar_question = vector_store.similarity_search(state["messages"][0].content)
        example_msg = HumanMessage(
            content=f"Here I provide a similar question and answer for reference: \n\n{similar_question[0].page_content}",
        )
        return {"messages": [Agent_prompt_template] + state["messages"] + [example_msg]}

    # Create graph
    builder = StateGraph(MessagesState)
    builder.add_node("retriever", retriever)
    builder.add_node("assistant", assistant)
    builder.add_node("tools", ToolNode(tools))

    builder.add_edge(START, "retriever")
    builder.add_edge("retriever", "assistant")
    builder.add_conditional_edges("assistant", tools_condition)
    builder.add_edge("tools", "assistant")

    # Compile and return the graph
    return builder.compile()

In [33]:
# test
if __name__ == "__main__":
    question = "When was attention is all you need paper printed and what is the main idea of it?"
    # Build the graph
    graph = build_graph()
    # Run the graph
    messages = [HumanMessage(content=question)]
    messages = graph.invoke({"messages": messages})
    for m in messages["messages"]:
        m.pretty_print()


================================ Human Message =================================

When was attention is all you need paper printed and what is the main idea of it?
================================ Human Message =================================

You are a helpful assistant following the REACT methodology and tasked with answering questions using a set of tools. 
Once a question is asked,you have to Report your thoughts, and finish your answer with the following template: 
FINAL ANSWER: [YOUR FINAL ANSWER]. 

### **Instructions:**  
- YOUR FINAL ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings. 
- If you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. 
- If you are asked for a string, don't use articles, neither abbreviations (e.g. for cities), and write the digits in plain text unless specified otherwise. If you are asked for a comma separated li

In [43]:
def build_graph():
    """Build the graph with traceable output using Groq + tools + vector search."""
    
    from langgraph.graph import StateGraph, START
    from langgraph.prebuilt import ToolNode
    from langchain_core.messages import HumanMessage
    from configs.prompt import Agent_prompt_template

    llm = ChatGroq(model="qwen-qwq-32b", temperature=0)
    llm_with_tools = llm.bind_tools(tools)

    def assistant(state: MessagesState):
        llm_response = llm_with_tools.invoke(state["messages"])
        step_log = {
            "step": "assistant",
            "tool_used": "LLM (Groq qwen-qwq-32b)",
            "input": state["messages"],
            "output": llm_response.content
        }
        return {
            "messages": [llm_response],
            "steps": state.get("steps", []) + [step_log]
        }

    def retriever(state: MessagesState):
        query = state["messages"][0].content
        similar_docs = vector_store.similarity_search(query)
        example_msg = HumanMessage(
            content=f"Here I provide a similar question and answer for reference:\n\n{similar_docs[0].page_content}",
        )
        step_log = {
            "step": "retriever",
            "tool_used": "Vector Store (Similarity Search)",
            "input": query,
            "output": similar_docs[0].page_content
        }
        return {
            "messages": [Agent_prompt_template] + state["messages"] + [example_msg],
            "steps": state.get("steps", []) + [step_log]
        }

    builder = StateGraph(MessagesState)
    builder.add_node("retriever", retriever)
    builder.add_node("assistant", assistant)
    builder.add_node("tools", ToolNode(tools))
    builder.add_edge(START, "retriever")
    builder.add_edge("retriever", "assistant")
    builder.add_conditional_edges("assistant", tools_condition)
    builder.add_edge("tools", "assistant")

    return builder.compile()

In [44]:
# test
if __name__ == "__main__":
    question = "What is the average temperature in Delhi in last week in celcius and are there any health tips?"
    # Build the graph
    graph = build_graph()
    # Run the graph
    messages = [HumanMessage(content=question)]
    messages = graph.invoke({"messages": messages})
    for m in messages["messages"]:
        m.pretty_print()



================================ Human Message =================================

What is the average temperature in Delhi in last week in celcius and are there any health tips?
================================ Human Message =================================

You are a helpful assistant following the REACT methodology and tasked with answering questions using a set of tools. 
Once a question is asked,you have to Report your thoughts, and finish your answer with the following template: 
FINAL ANSWER: [YOUR FINAL ANSWER]. 

### **Instructions:**  
- YOUR FINAL ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings. 
- If you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. 
- If you are asked for a string, don't use articles, neither abbreviations (e.g. for cities), and write the digits in plain text unless specified otherwise. If you are asked for a comm